In [1]:
!pip install bertopic datasets openai datamapplot

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.7/154.7 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.5/168.5 kB 22.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 51.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.3/18.3 MB 101.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.2/49.2 kB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 93.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 84.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.3/244.3 kB 30.9 MB/s eta 0:00:00
  Created wheel for Pyqtree: filename=Pyqtree-1.0.0-py3-none-any.whl size=5969 sha256=122eb533b9abe4e7e888fd192d7e2d57fe0b84fdc80399492bdca6c0d1ae2cb3
  Stored in directory: /root/.cache/pip/wheels/86/02/24/506ac193949f48c8bec599b613d722bd64a83063a190b3bff7
Successfully built Pyqtree
  Attempting uninstall: dask
    Found exis

In [2]:
# Load data from huggingface
from datasets import load_dataset
dataset = load_dataset("maartengr/arxiv_nlp")["train"]

# Extract metadata
abstracts = list(dataset["Abstracts"])
titles = list(dataset["Titles"])

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/617 [00:00<?, ?B/s]

data.csv:   0%|          | 0.00/53.2M [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [3]:
from sentence_transformers import SentenceTransformer

# Create an embedding for each abstract
embedding_model = SentenceTransformer('thenlper/gte-small')
embeddings = embedding_model.encode(abstracts, show_progress_bar=True)

modules.json:   0%|          | 0.00/385 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/57.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/583 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/66.7M [00:00<?, ?B/s]

...

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/1405 [00:00<?, ?it/s]

In [4]:
from umap import UMAP

# We reduce the input embeddings from 384 dimenions to 5 dimenions
umap_model = UMAP(
    n_components=5, min_dist=0.0, metric='cosine', random_state=42
)
reduced_embeddings = umap_model.fit_transform(embeddings)

/usr/local/lib/python3.12/dist-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(


In [6]:
from hdbscan import HDBSCAN

# We fit the model and extract the clusters
hdbscan_model = HDBSCAN(
    min_cluster_size=50, metric='euclidean', cluster_selection_method='eom'
).fit(reduced_embeddings)
clusters = hdbscan_model.labels_


BERTopic: A Modular Topic Modeling Framework

In [7]:
from bertopic import BERTopic

# Train our model with our previously defined models
topic_model = BERTopic(
    embedding_model=embedding_model,
    umap_model=umap_model,
    hdbscan_model=hdbscan_model,
    verbose=True
).fit(abstracts, embeddings)

2026-02-19 14:45:43,575 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2026-02-19 14:46:31,831 - BERTopic - Dimensionality - Completed ✓
2026-02-19 14:46:31,833 - BERTopic - Cluster - Start clustering the reduced embeddings
2026-02-19 14:46:33,942 - BERTopic - Cluster - Completed ✓
2026-02-19 14:46:33,965 - BERTopic - Representation - Fine-tuning topics using representation models.
2026-02-19 14:46:37,680 - BERTopic - Representation - Completed ✓


In [8]:
topic_model.get_topic_info()

Topic  Count                                          Name  \
0       -1  14292                              -1_the_of_and_to   
1        0   2244                0_question_questions_answer_qa   
2        1   2073                  1_speech_asr_recognition_end   
3        2   1435         2_medical_clinical_biomedical_patient   
4        3   1046              3_translation_nmt_machine_neural   
..     ...    ...                                           ...   
149    148     52          148_counseling_mental_therapy_health   
150    149     51  149_diffusion_generation_autoregressive_text   
151    150     50      150_multimodal_sentiment_modality_fusion   
152    151     50               151_rumor_rumour_rumors_rumours   
153    152     50     152_prompt_prompts_optimization_prompting   

                                        Representation  \
0    [the, of, and, to, in, we, language, for, that...   
1    [question, questions, answer, qa, answering, a...   
2    [speech, asr, recognition, end, acoustic, spea...   
3    [medical, clinical, biomedical, patient, healt...   
4    [translation, nmt, machine, neural, bleu, engl...   
..                                                 ...   
149  [counseling, mental, therapy, health, psychoth...   
150  [diffusion, generation, autoregressive, text, ...   
151  [multimodal, sentiment, modality, fusion, moda...   
152  [rumor, rumour, rumors, rumours, stance, verac...   
153  [prompt, prompts, optimization, prompting, llm...   

                                   Representative_Docs  
0    [  Understanding context is key to understandi...  
1    [  In recent years, there have been amazing ad...  
2    [  Conversational context information, higher-...  
3    [  A common practice in the medical industry i...  
4    [  Neural machine translation~(NMT) is ineffec...  
..                                                 ...  
149  [  Mental health care poses an increasingly se...  
150  [  Diffusion models have achieved great succes...  
151  [  Multimodal sentiment analysis is an importa...  
152  [  The rapid development of social media chang...  
153  [  Prompt optimization aims to find the best p...  

[154 rows x 5 columns]

In [9]:
topic_model.get_topic(0)

[('question', np.float64(0.02101040039308071)),
 ('questions', np.float64(0.015688719453758684)),
 ('answer', np.float64(0.015636224577210124)),
 ('qa', np.float64(0.015620537718276761)),
 ('answering', np.float64(0.01461366109709343)),
 ('answers', np.float64(0.009846992928574144)),
 ('retrieval', np.float64(0.009428958578309974)),
 ('comprehension', np.float64(0.007735707649367827)),
 ('reading', np.float64(0.00716539953507451)),
 ('the', np.float64(0.006251157623024926))]

In [10]:
topic_model.find_topics("topic modeling")

([23, -1, 47, 2, 34],
 [np.float64(0.9546342246269499),
  np.float64(0.9116719482232511),
  np.float64(0.9077332723011932),
  np.float64(0.9076265211760097),
  np.float64(0.9049669001025927)])

In [11]:
topic_model.get_topic(22)

[('commonsense', np.float64(0.07215029720071144)),
 ('knowledge', np.float64(0.02471360995856926)),
 ('reasoning', np.float64(0.01999251641512859)),
 ('graph', np.float64(0.006990954080458458)),
 ('models', np.float64(0.006772506252840321)),
 ('graphs', np.float64(0.006703373374388432)),
 ('that', np.float64(0.006619952189740844)),
 ('answering', np.float64(0.006429045924779322)),
 ('question', np.float64(0.006380043155000866)),
 ('conceptnet', np.float64(0.006248922119891975))]

In [12]:
topic_model.topics_[titles.index('BERTopic: Neural topic modeling with a class-based TF-IDF procedure')]

23

Visualizations

In [13]:
# Visualize topics and documents
fig = topic_model.visualize_documents(
    titles,
    reduced_embeddings=reduced_embeddings,
    width=1200,
    hide_annotations=True
)

# Update fonts of legend for easier visualization
fig.update_layout(font=dict(size=16))

In [ ]:
# Visualize barchart with ranked keywords
topic_model.visualize_barchart()

# Visualize relationships between topics
topic_model.visualize_heatmap(n_clusters=30)

# Visualize the potential hierarchical structure of topics
topic_model.visualize_hierarchy()